## Learning Rate Calibration of Gradient Descent in PyBOP

In this notebook, we calibrate the learning rate for the gradient descent optimiser on a parameter identification problem. The gradient descent learning rate is taken as the `sigma` value passed to the optimiser class.

### Setting up the Environment

Before we begin, we need to ensure that we have all the necessary tools. We will install PyBOP and upgrade dependencies:

In [ ]:
%pip install --upgrade pip ipywidgets -q
%pip install pybop -q

/home/nicola/GitHub/PyBOP/.nox/notebooks-overwrite/bin/python3: No module named pip


Note: you may need to restart the kernel to use updated packages.
/home/nicola/GitHub/PyBOP/.nox/notebooks-overwrite/bin/python3: No module named pip


Note: you may need to restart the kernel to use updated packages.


### Importing Libraries

With the environment set up, we can now import PyBOP alongside other libraries we will need:

In [ ]:
import numpy as np
import pybamm

import pybop

pybop.plot.PlotlyManager().pio.renderers.default = "notebook_connected"

Let's fix the random seed in order to generate consistent output during development, although this does not need to be done in practice.

In [ ]:
np.random.seed(8)

## Generating Synthetic Data

To demonstrate parameter estimation, we first need some data. We will generate synthetic data using a forward model, which requires defining a parameter set and the model itself.

### Defining Parameters and Model

We start by creating an example parameter set, constructing the single-particle model (SPM) and generating the synthetic data.

In [ ]:
model = pybamm.lithium_ion.SPM()
parameter_values = pybamm.ParameterValues("Chen2020")
parameter_values.update(
    {
        "Negative electrode active material volume fraction": 0.65,
        "Positive electrode active material volume fraction": 0.51,
    }
)
parameter_values.set_initial_state(0.4)
experiment = pybamm.Experiment(
    [
        "Discharge at 0.5C for 6 minutes (4 second period)",
        "Charge at 0.5C for 6 minutes (4 second period)",
    ]
    * 2
)
sol = pybamm.Simulation(
    model, parameter_values=parameter_values, experiment=experiment
).solve()

### Adding Noise to Voltage Data

To make the parameter estimation more realistic, we add Gaussian noise to the data.

In [ ]:
sigma = 0.002
corrupt_values = sol["Voltage [V]"].data + np.random.normal(0, sigma, len(sol.t))

## Identifying the Parameters

We will now set up the parameter estimation process by defining the datasets for optimisation and selecting the model parameters we wish to estimate.

### Creating a Dataset

The dataset for optimisation is composed of time, current, and the noisy voltage data:

In [ ]:
dataset = pybop.Dataset(
    {
        "Time [s]": sol.t,
        "Current function [A]": sol["Current [A]"].data,
        "Voltage [V]": corrupt_values,
    }
)

### Defining Parameters to Estimate

We select the parameters for estimation and set up their prior distributions and bounds:

In [ ]:
parameter_values.update(
    {
        "Negative electrode active material volume fraction": pybop.Parameter(
            prior=pybop.Uniform(0.45, 0.7),
        ),
        "Positive electrode active material volume fraction": pybop.Parameter(
            prior=pybop.Uniform(0.45, 0.7),
        ),
    }
)

### Setting up the Optimisation Problem with incorrect sigma value

With the datasets and parameters defined, we can set up the optimisation problem, its cost function, and the optimiser. For gradient descent, the `sigma` value corresponds to the learning rate. Let's set this hyperparmeter incorrectly to view how we calibrate it. In this example, let's start with `sigma=0.2`.

In [ ]:
simulator = pybop.pybamm.Simulator(
    model, parameter_values=parameter_values, protocol=dataset
)
cost = pybop.SumSquaredError(dataset)
problem = pybop.Problem(simulator, cost)
options = pybop.PintsOptions(sigma=0.2, max_iterations=100)
optim = pybop.GradientDescent(problem, options=options)

NOTE: Boundaries ignored by <class 'pybop.optimisers._gradient_descent.GradientDescentImpl'>


### Running the Optimisation

We proceed to run the optimisation algorithm to estimate the parameters with the updated learning rate (`sigma`).

In [ ]:
result = optim.run()

### Viewing the Estimated Parameters

After the optimisation, we can examine the estimated parameter values. In this case, the optimiser misses the optimal solution by a large amount.

In [ ]:
result.x  # This will output the estimated parameters

array([0.64963544, 0.50976788])

Let's plot the time-series prediction for the given solution. As we suspected, the optimiser found a very poor solution. 

In [ ]:
pybop.plot.problem(problem, problem_inputs=result.x, title="Optimised Comparison");

## Calibrating the Learning Rate 

Now that we've seen how poor an incorrect `sigma` value is for this optimisation problem, let's calibrate this value to find the optimal solution in the lowest number of iterations.

In [ ]:
sigmas = np.linspace(0.02, 0.25, 6)  # Change this to a smaller range for a quicker run
results = []
for sigma in sigmas:
    print(sigma)
    simulator = pybop.pybamm.Simulator(
        model, parameter_values=parameter_values, protocol=dataset
    )
    cost = pybop.SumSquaredError(dataset)
    problem = pybop.Problem(simulator, cost)
    options = pybop.PintsOptions(sigma=sigma, max_iterations=100)
    optim = pybop.GradientDescent(problem, options=options)
    result = optim.run()
    results.append(result)

0.02


NOTE: Boundaries ignored by <class 'pybop.optimisers._gradient_descent.GradientDescentImpl'>


0.066


NOTE: Boundaries ignored by <class 'pybop.optimisers._gradient_descent.GradientDescentImpl'>


0.112


...

NOTE: Boundaries ignored by <class 'pybop.optimisers._gradient_descent.GradientDescentImpl'>


0.204


NOTE: Boundaries ignored by <class 'pybop.optimisers._gradient_descent.GradientDescentImpl'>


0.25


NOTE: Boundaries ignored by <class 'pybop.optimisers._gradient_descent.GradientDescentImpl'>


In [ ]:
for result, sigma in zip(results, sigmas, strict=False):
    print(
        f"| Sigma: {sigma} | Num Iterations: {result.n_iterations} | Best Cost: {result.best_cost} | Results: {result.x} |"
    )

| Sigma: 0.02 | Num Iterations: 100 | Best Cost: 0.0025855997446332353 | Results: [0.61365307 0.55015249] |
| Sigma: 0.066 | Num Iterations: 92 | Best Cost: 0.001599260574539559 | Results: [0.64788512 0.51144791] |
| Sigma: 0.112 | Num Iterations: 62 | Best Cost: 0.0015965948393614196 | Results: [0.64907284 0.51033483] |
| Sigma: 0.158 | Num Iterations: 47 | Best Cost: 0.001596197916163161 | Results: [0.64933458 0.51009304] |
| Sigma: 0.204 | Num Iterations: 39 | Best Cost: 0.0015951231544535423 | Results: [0.64963664 0.50976719] |
| Sigma: 0.25 | Num Iterations: 36 | Best Cost: 0.0015956899688338425 | Results: [0.64944735 0.5099636 ] |


`Sigma=0.204` produces the lowest final cost, as it balances fast convergence with a small enough step size to avoid jumping over fine changes in the landscape. An additional way view this information is to plot the optimiser convergences,

In [ ]:
for result, sigma in zip(results, sigmas, strict=False):
    result.plot_convergence(title=f"Sigma: {sigma}")
    result.plot_parameters()

### Cost Landscapes

Finally, we can visualise the cost landscape and the path taken by the optimiser:

In [ ]:
# Plot the cost landscape with optimisation path and updated bounds
bounds = np.array([[0.4, 0.8], [0.4, 0.8]])
for result, sigma in zip(results, sigmas, strict=False):
    result.plot_surface(bounds=bounds, title=f"Sigma: {sigma}")

### The Optimal Time-series Trajectory

Let's take `sigma = 0.204` as the best learning rate for this problem and look at the time-series trajectories.

In [ ]:
pybop.plot.problem(problem, problem_inputs=results[-2].x, title="Optimised Comparison");

### Conclusion

This notebook covers how to calibrate the learning rate for the gradient descent optimiser. This provides an introduction into hyperparameter tuning that will be discussed in further notebooks.